# Exploración de bow_mpi.csv y bow_serial.csv
Carga y explora las matrices bolsa de palabras generadas por el proyecto. Puedes alternar entre los dos CSV en `results/`, filtrar columnas por palabra clave y revisar los conteos por documento.


In [7]:
from pathlib import Path
import pandas as pd
from IPython.display import display


def find_results_dir() -> Path:
    """Ubica el directorio results desde el notebook o su padre inmediato."""
    here = Path.cwd()
    if (here / "results").exists():
        return here / "results"
    if (here.parent / "results").exists():
        return here.parent / "results"
    raise FileNotFoundError("No se encontró la carpeta results junto al notebook.")


RESULTS_DIR = find_results_dir()
FILES = {
    "bow_mpi.csv": RESULTS_DIR / "bow_mpi.csv",
    "bow_serial.csv": RESULTS_DIR / "bow_serial.csv",
}


def load_csv(path: Path) -> pd.DataFrame:
    df = pd.read_csv(path)
    df.columns = df.columns.str.strip()
    return df


In [8]:
df_mpi = load_csv(FILES["bow_mpi.csv"])
df_serial = load_csv(FILES["bow_serial.csv"])

same_shape = df_mpi.shape == df_serial.shape
same_content = df_mpi.equals(df_serial)

print(f"Misma forma: {same_shape} ({df_mpi.shape})")
print(f"Contenido idéntico: {same_content}")

if not same_content:
    differing_cols = [c for c in df_mpi.columns if not df_mpi[c].equals(df_serial[c])]
    print(f"Columnas con diferencias (primeras 10): {differing_cols[:10]}")


Misma forma: True ((6, 15192))
Contenido idéntico: True


In [9]:
# Vista en bruto de bow_mpi.csv
pd.set_option("display.max_columns", 20)
display(df_mpi.head())


document  0  000  00033  04  08  0em   1  10  100  \
0     dickens_a_christmas_carol.txt  7    1      1   0   0    0  47   2    2   
1  dickens_a_tale_of_two_cities.txt  7    1      0   0   0    0  46   2    0   
2          dickens_oliver_twist.txt  6    1      0   0   0    2  47   0    0   
3            shakespeare_hamlet.txt  4    3      0   1   0    0  10   2    3   
4      shakespeare_romeo_juliet.txt  4    3      0   0   1    0  26   2    1   

   ...  youth  youthful  youthfulness  z  zeal  zealous  zenith  zip  zone  \
0  ...      1         0             0  0     1        0       0    1     0   
1  ...     10         3             1  0     0        2       0    1     0   
2  ...      9         6             0  1     0        2       1    0     0   
3  ...     14         0             0  0     0        0       0    2     1   
4  ...      6         3             0  0     0        0       0    1     0   

   zounds  
0       0  
1       0  
2       0  
3       0  
4       2  

[5 rows x 15192 columns]

In [10]:
# Vista en bruto de bow_serial.csv
pd.set_option("display.max_columns", 20)
display(df_serial.head())


document  0  000  00033  04  08  0em   1  10  100  \
0     dickens_a_christmas_carol.txt  7    1      1   0   0    0  47   2    2   
1  dickens_a_tale_of_two_cities.txt  7    1      0   0   0    0  46   2    0   
2          dickens_oliver_twist.txt  6    1      0   0   0    2  47   0    0   
3            shakespeare_hamlet.txt  4    3      0   1   0    0  10   2    3   
4      shakespeare_romeo_juliet.txt  4    3      0   0   1    0  26   2    1   

   ...  youth  youthful  youthfulness  z  zeal  zealous  zenith  zip  zone  \
0  ...      1         0             0  0     1        0       0    1     0   
1  ...     10         3             1  0     0        2       0    1     0   
2  ...      9         6             0  1     0        2       1    0     0   
3  ...     14         0             0  0     0        0       0    2     1   
4  ...      6         3             0  0     0        0       0    1     0   

   zounds  
0       0  
1       0  
2       0  
3       0  
4       2  

[5 rows x 15192 columns]

In [11]:
import ipywidgets as widgets


def filter_columns(df: pd.DataFrame, word: str, max_default: int = 10) -> pd.DataFrame:
    if not word:
        cols = df.columns[: max_default + 1]  # document + primeras columnas
        return df.loc[:, cols]
    word_lower = word.lower()
    exact = [c for c in df.columns if c.lower() == word_lower]
    partial = [c for c in df.columns if word_lower in c.lower() and c.lower() != word_lower]
    ordered = exact + partial
    if not ordered:
        return pd.DataFrame({"mensaje": [f"No se encontraron columnas con '{word}'."]})
    cols = ["document"] + ordered
    return df.loc[:, cols]


def render_table(*_):
    output.clear_output()
    selection = file_dropdown.value
    word = search_box.value.strip()
    df = load_csv(FILES[selection])
    filtered = filter_columns(df, word)
    with output:
        if word:
            print(f'Filtrado por palabra clave: "{word}"')
        else:
            print("Mostrando las primeras columnas del CSV (sin filtro)")
        styled = filtered.head(25).style.set_table_attributes(
            'style="display:block; overflow-x:auto; white-space: nowrap;"'
        )
        display(styled)


file_dropdown = widgets.Dropdown(options=list(FILES.keys()), value="bow_mpi.csv", description="Archivo:")
search_box = widgets.Text(description="Palabra:", placeholder="youth")
refresh_button = widgets.Button(description="Actualizar", button_style="primary")

output = widgets.Output()

file_dropdown.observe(render_table, names="value")
search_box.observe(lambda change: render_table(), names="value")
refresh_button.on_click(render_table)

controls = widgets.HBox([file_dropdown, search_box, refresh_button])
display(controls, output)
render_table()


Output()

### Cómo usar
- Ejecuta la celda de configuración y la de verificación para cargar los datos.
- Las siguientes dos celdas muestran las primeras filas de cada CSV en bruto.
- La última celda despliega widgets interactivos para seleccionar CSV y filtrar columnas por palabra clave (vacío muestra las primeras 10 columnas). Si existe un match exacto, se muestra primero.

Si prefieres una interfaz tipo Data Wrangler, abre el archivo desde VS Code y elige "Open in Data Wrangler"; la tabla se cargará con filtros similares.
